## Downloading all the required libraries

In [1]:
import numpy as np 

import pandas as pd 
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json #

!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim

import requests
from pandas.io.json import json_normalize 


import matplotlib.cm as cm
import matplotlib.colors as colors


from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes 
import folium

Solving environment: done

## Package Plan ##

  environment location: /home/jupyterlab/conda/envs/python

  added / updated specs:
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    geographiclib-1.50         |             py_0          34 KB  conda-forge
    geopy-1.21.0               |             py_0          58 KB  conda-forge
    openssl-1.1.1g             |       h516909a_0         2.1 MB  conda-forge
    ------------------------------------------------------------
                                           Total:         2.2 MB

The following NEW packages will be INSTALLED:

  geographiclib      conda-forge/noarch::geographiclib-1.50-py_0
  geopy              conda-forge/noarch::geopy-1.21.0-py_0

The following packages will be UPDATED:

  openssl                                 1.1.1f-h516909a_0 --> 1.1.1g-h516909a_0



openssl-1.1.1g       | 2.1 MB    | ############

## Loading the dataset containing the neighborhoods of mumbai

In [2]:
df_mumbai = pd.read_csv('MumbaI_Neighborhood_data (1).csv')

In [3]:
df_mumbai.head()

Unnamed: 0          Location  Pincode        State District   Latitude  \
0         NaN  A I staff colony   400029  Maharashtra   Mumbai  19.078700   
1         NaN  Aareymilk Colony   400065  Maharashtra   Mumbai  19.148509   
2         NaN          Agripada   400011  Maharashtra   Mumbai  18.984810   
3         NaN           Airport   400099  Maharashtra   Mumbai  19.090052   
4         NaN          Ambewadi   400004  Maharashtra   Mumbai  18.963010   

   Longitude  
0  72.860050  
1  72.881740  
2  72.816860  
3  72.868672  
4  72.823040

In [4]:
df_mumbai.drop('Unnamed: 0', axis=1, inplace=True)

In [5]:
df_mumbai.head()

Location  Pincode        State District   Latitude  Longitude
0  A I staff colony   400029  Maharashtra   Mumbai  19.078700  72.860050
1  Aareymilk Colony   400065  Maharashtra   Mumbai  19.148509  72.881740
2          Agripada   400011  Maharashtra   Mumbai  18.984810  72.816860
3           Airport   400099  Maharashtra   Mumbai  19.090052  72.868672
4          Ambewadi   400004  Maharashtra   Mumbai  18.963010  72.823040

## Finding the latitude and longitude of Mumbai

In [6]:
address = 'Mumbai'

geolocator = Nominatim(user_agent="to_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Mumbai are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Mumbai are 18.9387711, 72.8353355.


## Creating a map

In [10]:
map_mum = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, loca, pin in zip(df_mumbai['Latitude'], df_mumbai['Longitude'], df_mumbai['Location'], df_mumbai['Pincode']):
    label = '{}, {}'.format(loca, pin)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_mum)  
    
map_mum

## Foursquare Credentials and Version

In [11]:
CLIENT_ID = 'J1QUBNPCUUS3TGMKMY12UEMMVN0ZZAB2SSBD4OJ3P0V4GPKW' # your Foursquare ID
CLIENT_SECRET = 'UW3NKX4SWAXJNFWVOASG2ECYGXCDES2B2BWL5MZXDLULMFRS' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: J1QUBNPCUUS3TGMKMY12UEMMVN0ZZAB2SSBD4OJ3P0V4GPKW
CLIENT_SECRET:UW3NKX4SWAXJNFWVOASG2ECYGXCDES2B2BWL5MZXDLULMFRS


## Getting Nearby Venues

In [14]:
radius=500
LIMIT=100
venues_list=[]
    
for lat,lng,loca,post in zip(df_mumbai['Latitude'], df_mumbai['Longitude'], df_mumbai['Location'], df_mumbai['Pincode']):
            
        
    url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        
    results = requests.get(url).json()["response"]['groups'][0]['items']
        
    for v in results:
        venues_list.append((
            post, 
            loca,
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']))   


In [15]:
df_with_venues = pd.DataFrame(venues_list)
df_with_venues.columns = ['Pincode', 'Location', 'Latitude', 'Longitude', 'Venue_Name', 'Venue_Latitude', 'Venue_Longitude', 'Venue_Category']
df_with_venues.head()

Pincode          Location  Latitude  Longitude           Venue_Name  \
0   400029  A I staff colony  19.07870   72.86005  Natural's Ice Cream   
1   400029  A I staff colony  19.07870   72.86005    Geeta Vihar Hotel   
2   400029  A I staff colony  19.07870   72.86005      Kalina bus stop   
3   400029  A I staff colony  19.07870   72.86005        Chetan Punjab   
4   400011          Agripada  18.98481   72.81686              Gallops   

   Venue_Latitude  Venue_Longitude     Venue_Category  
0       19.077560        72.863035     Ice Cream Shop  
1       19.078022        72.862714  Indian Restaurant  
2       19.076665        72.862189        Bus Station  
3       19.081774        72.857418                Bar  
4       18.981231        72.817178         Restaurant

## Number of venues per Location

In [16]:
df_with_venues.groupby("Location").count()

Pincode  Latitude  Longitude  Venue_Name  \
Location                                                              
A I staff colony                 4         4          4           4   
Agripada                        12        12         12          12   
Airport                          4         4          4           4   
Ambewadi                         4         4          4           4   
Andheri                         19        19         19          19   
Andheri East                    12        12         12          12   
Andheri Railway station         12        12         12          12   
Antop Hill                       4         4          4           4   
Asvini                           1         1          1           1   
Azad Nagar                      12        12         12          12   
B P t colony                     4         4          4           4   
B.N. bhavan                      7         7          7           7   
B.P.lane                        42        42         42          42   
Bandra West                     48        48         48          48   
Bandra(east)                    48        48         48          48   
Bazargate                       31        31         31          31   
Best Staff colony                4         4          4           4   
Bharat Nagar                    48        48         48          48   
Bhawani Shankar                 31        31         31          31   
Bhawani Shankar rd              31        31         31          31   
Borivali East                    6         6          6           6   
Borvali West                     6         6          6           6   
C G s colony                     4         4          4           4   
Central Building                29        29         29          29   
Century Mill                     4         4          4           4   
Chakala Midc                     7         7          7           7   
Chamarbaug                      31        31         31          31   
Charkop                          5         5          5           5   
Charni Road                      4         4          4           4   
Chaupati                         4         4          4           4   
Chinchbunder                     8         8          8           8   
Chinchpokli                      4         4          4           4   
Churchgate                      50        50         50          50   
Colaba                           3         3          3           3   
Cotton Exchange                  9         9          9           9   
Cumballa Hill                   24        24         24          24   
Cumballa Sea face               24        24         24          24   
Dadar                           20        20         20          20   
Dadar Colony                    20        20         20          20   
Dahisar                          6         6          6           6   
Dahisar Rs                       1         1          1           1   
Danda                           23        23         23          23   
Daulat Nagar                     2         2          2           2   
Dharavi                          2         2          2           2   
Dharavi Road                     2         2          2           2   
Dockyard Road                    1         1          1           1   
Dr Deshmukh marg                 4         4          4           4   
Falkland Road                    4         4          4           4   
Girgaon                         27        27         27          27   
Gokhale Road                    21        21         21          21   
Goregaon East                   10        10         10          10   
Government Colony                7         7          7           7   
Gowalia Tank                    16        16         16          16   
Grant Road                      48        48         48          48   
H.M.p. school                   22        22       

## Check if there are Italian Restaurants in the Venue Categories

In [17]:
"Italian Restaurant" in df_with_venues['Venue_Category'].unique()

True

## Analysing Locations

In [19]:
mum_onehot = pd.get_dummies(df_with_venues[['Venue_Category']], prefix="", prefix_sep="")
mum_onehot['Location'] = df_with_venues['Location']
fixed_columns = [mum_onehot.columns[-1]] + list(mum_onehot.columns[:-1])
mum_onehot = mum_onehot[fixed_columns]
mum_onehot.head()

Location  ATM  Accessories Store  Airport  Airport Lounge  \
0  A I staff colony    0                  0        0               0   
1  A I staff colony    0                  0        0               0   
2  A I staff colony    0                  0        0               0   
3  A I staff colony    0                  0        0               0   
4          Agripada    0                  0        0               0   

   Airport Terminal  Amphitheater  Antique Shop  Aquarium  Arcade  \
0                 0             0             0         0       0   
1                 0             0             0         0       0   
2                 0             0             0         0       0   
3                 0             0             0         0       0   
4                 0             0             0         0       0   

   Art Gallery  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0            0                    0                 0                   0   
1            0                    0                 0                   0   
2            0                    0                 0                   0   
3            0                    0                 0                   0   
4            0                    0                 0                   0   

   Automotive Shop  BBQ Joint  Bagel Shop  Bakery  Bank  Bar  Beach  \
0                0          0           0       0     0    0      0   
1                0          0           0       0     0    0      0   
2                0          0           0       0     0    0      0   
3                0          0           0       0     0    1      0   
4                0          0           0       0     0    0      0   

   Bed & Breakfast  Beer Bar  Beer Garden  Bengali Restaurant  Bistro  \
0                0         0            0                   0       0   
1                0         0            0                   0       0   
2                0         0            0                   0       0   
3                0         0            0                   0       0   
4                0         0            0                   0       0   

   Bookstore  Boutique  Breakfast Spot  Brewery  Bridal Shop  Burger Joint  \
0          0         0               0        0            0             0   
1          0         0               0        0            0             0   
2          0         0               0        0            0             0   
3          0         0               0        0            0             0   
4          0         0               0        0            0             0   

   Bus Station  Business Service  Café  Chaat Place  Cheese Shop  \
0            0                 0     0            0            0   
1            0                 0     0            0            0   
2            1                 0     0            0            0   
3            0                 0     0            0            0   
4            0                 0     0            0            0   

   Chinese Restaurant  Clothing Store  Club House  Cocktail Bar  Coffee Shop  \
0                   0               0           0             0            0   
1                   0               0           0             0            0   
2                   0               0           0             0            0   
3                   0               0           0             0            0   
4                   0               0           0             0            0   

   College Academic Building  College Auditorium  Comfort Food Restaurant  \
0                          0                   0                        0   
1                          0                   0                        0   
2                          0                   0                        0   
3                          0                   0                        0   
4                          0                   0                        0   

   Concert H

## Group rows by location and by taking the mean of the frequency of occurrence of each category

In [21]:
mum_grouped = mum_onehot.groupby(['Location']).mean().reset_index()
mum_grouped.head()

Location  ATM  Accessories Store  Airport  Airport Lounge  \
0  A I staff colony  0.0                0.0     0.00            0.00   
1          Agripada  0.0                0.0     0.00            0.00   
2           Airport  0.0                0.0     0.25            0.25   
3          Ambewadi  0.0                0.0     0.00            0.00   
4           Andheri  0.0                0.0     0.00            0.00   

   Airport Terminal  Amphitheater  Antique Shop  Aquarium  Arcade  \
0               0.0           0.0           0.0       0.0     0.0   
1               0.0           0.0           0.0       0.0     0.0   
2               0.0           0.0           0.0       0.0     0.0   
3               0.0           0.0           0.0       0.0     0.0   
4               0.0           0.0           0.0       0.0     0.0   

   Art Gallery  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0     0.000000                  0.0               0.0                 0.0   
1     0.166667                  0.0               0.0                 0.0   
2     0.000000                  0.0               0.0                 0.0   
3     0.000000                  0.0               0.0                 0.0   
4     0.000000                  0.0               0.0                 0.0   

   Automotive Shop  BBQ Joint  Bagel Shop  Bakery  Bank       Bar  Beach  \
0              0.0        0.0    0.000000    0.00   0.0  0.250000    0.0   
1              0.0        0.0    0.000000    0.00   0.0  0.000000    0.0   
2              0.0        0.0    0.000000    0.25   0.0  0.000000    0.0   
3              0.0        0.0    0.000000    0.00   0.0  0.000000    0.0   
4              0.0        0.0    0.052632    0.00   0.0  0.052632    0.0   

   Bed & Breakfast  Beer Bar  Beer Garden  Bengali Restaurant  Bistro  \
0              0.0       0.0          0.0                 0.0     0.0   
1              0.0       0.0          0.0                 0.0     0.0   
2              0.0       0.0          0.0                 0.0     0.0   
3              0.0       0.0          0.0                 0.0     0.0   
4              0.0       0.0          0.0                 0.0     0.0   

   Bookstore  Boutique  Breakfast Spot  Brewery  Bridal Shop  Burger Joint  \
0        0.0       0.0             0.0      0.0          0.0           0.0   
1        0.0       0.0             0.0      0.0          0.0           0.0   
2        0.0       0.0             0.0      0.0          0.0           0.0   
3        0.0       0.0             0.0      0.0          0.0           0.0   
4        0.0       0.0             0.0      0.0          0.0           0.0   

   Bus Station  Business Service      Café  Chaat Place  Cheese Shop  \
0         0.25               0.0  0.000000          0.0          0.0   
1         0.00               0.0  0.000000          0.0          0.0   
2         0.00               0.0  0.000000          0.0          0.0   
3         0.00               0.0  0.000000          0.0          0.0   
4         0.00               0.0  0.105263          0.0          0.0   

   Chinese Restaurant  Clothing Store  Club House  Cocktail Bar  Coffee Shop  \
0                 0.0             0.0         0.0           0.0     0.000000   
1                 0.0             0.0         0.0           0.0     0.000000   
2                 0.0             0.0         0.0           0.0     0.250000   
3                 0.0             0.0         0.0           0.0     0.000000   
4                 0.0             0.0         0.0           0.0     0.052632   

   College Academic Building  College Auditorium  Comfort Food Restaurant  \
0                        0.0                 0.0                      0.0   
1                        0.0                 0.0                      0.0   
2                        0.0                 0.0                      0.0   
3                        0.0                 0.0                      0.0   
4                        0.0        

## Only Italian Restaurants

In [22]:
mum_italian = mum_grouped[['Location', 'Italian Restaurant']]
mum_italian.head()

Location  Italian Restaurant
0  A I staff colony            0.000000
1          Agripada            0.083333
2           Airport            0.000000
3          Ambewadi            0.000000
4           Andheri            0.000000

## Clustering

In [25]:
kclusters = 4
mum_cluster = mum_italian.drop('Location', axis=1)
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(mum_cluster)
kmeans.labels_[0:10]


array([0, 3, 0, 0, 0, 0, 0, 0, 0, 0], dtype=int32)

## Creating new dataframe

In [30]:
mum_merged = mum_italian.copy()
mum_merged['Cluster Labels'] = kmeans.labels_
mum_merged = mum_merged.join(df_with_venues.set_index('Location'), on='Location')
mum_merged.head()
mum_merged.drop(['Latitude', 'Longitude'], axis=1, inplace=True)

In [31]:
mum_merged.head()

Location  Italian Restaurant  Cluster Labels  Pincode  \
0  A I staff colony            0.000000               0   400029   
0  A I staff colony            0.000000               0   400029   
0  A I staff colony            0.000000               0   400029   
0  A I staff colony            0.000000               0   400029   
1          Agripada            0.083333               3   400011   

            Venue_Name  Venue_Latitude  Venue_Longitude     Venue_Category  
0  Natural's Ice Cream       19.077560        72.863035     Ice Cream Shop  
0    Geeta Vihar Hotel       19.078022        72.862714  Indian Restaurant  
0      Kalina bus stop       19.076665        72.862189        Bus Station  
0        Chetan Punjab       19.081774        72.857418                Bar  
1              Gallops       18.981231        72.817178         Restaurant

## Visualizing Clusters

In [32]:

map_clusters = folium.Map(location=[latitude, longitude], zoom_start=10)


x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]


markers_colors = []
for lat, lon, loca, cluster in zip(mum_merged['Venue_Latitude'],mum_merged['Venue_Longitude'], mum_merged['Location'], mum_merged['Cluster Labels']):
    label = folium.Popup(str(loca) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## Examining Clusters

In [33]:
mum_merged.loc[mum_merged['Cluster Labels'] == 0, mum_merged.columns[[1] + list(range(5, mum_merged.shape[1]))]]

Italian Restaurant  Venue_Latitude  Venue_Longitude  \
0              0.000000       19.077560        72.863035   
0              0.000000       19.078022        72.862714   
0              0.000000       19.076665        72.862189   
0              0.000000       19.081774        72.857418   
2              0.000000       19.091774        72.868675   
2              0.000000       19.090509        72.865148   
2              0.000000       19.090022        72.868714   
2              0.000000       19.092619        72.866320   
3              0.000000       18.961417        72.823379   
3              0.000000       18.961581        72.823527   
3              0.000000       18.963412        72.824964   
3              0.000000       18.964676        72.819528   
4              0.000000       19.114538        72.836204   
4              0.000000       19.115305        72.834501   
4              0.000000       19.115056        72.834496   
4              0.000000       19.115078        72.834366   
4              0.000000       19.114569        72.836205   
4              0.000000       19.113633        72.834702   
4              0.000000       19.112690        72.837682   
4              0.000000       19.114442        72.836140   
4              0.000000       19.115439        72.834728   
4              0.000000       19.114483        72.831274   
4              0.000000       19.114644        72.836352   
4              0.000000       19.114332        72.836460   
4              0.000000       19.114709        72.836158   
4              0.000000       19.114569        72.836168   
4              0.000000       19.115018        72.836157   
4              0.000000       19.116724        72.834126   
4              0.000000       19.114499        72.834139   
4              0.000000       19.116114        72.832395   
4              0.000000       19.116091        72.831790   
5              0.000000       19.111258        72.869820   
5              0.000000       19.117567        72.867485   
5              0.000000       19.109283        72.869891   
5              0.000000       19.112000        72.867000   
5              0.000000       19.111632        72.871314   
5              0.000000       19.111768        72.867730   
5              0.000000       19.111247        72.870980   
5              0.000000       19.112325        72.867943   
5              0.000000       19.110905        72.866818   
5              0.000000       19.111798        72.870948   
5              0.000000       19.112473        72.866251   
5              0.000000       19.110523        72.866643   
6              0.000000       19.111258        72.869820   
6              0.000000       19.117567        72.867485   
6              0.000000       19.109283        72.869891   
6              0.000000       19.112000        72.867000   
6              0.000000       19.111632        72.871314   
6              0.000000       19.111768        72.867730   
6              0.000000       19.111247        72.870980   
6              0.000000       19.112325        72.867943   
6              0.000000       19.110905        72.866818   
6              0.000000       19.111798        72.870948   
6              0.000000       19.112473        72.866251   
6              0.000000       19.110523        72.866643   
7              0.000000       19.022163        72.863034   
7              0.000000       19.018984        72.865363   
7              0.000000       19.022335        72.862039   
7              0.000000       19.018421        72.864422   
8              0.000000       18.897406        72.809242   
9              0.000000       19.128122        72.825384   
9              0.000000       19.126762        72.830001   
9              0.000000       19.127750        72.827595   
9              0.000000       19.128816        72.827619   
9              0.000000       19.126735        72.825160   
9              0.000000       19.131221      

In [34]:
mum_merged.loc[mum_merged['Cluster Labels'] == 1, mum_merged.columns[[1] + list(range(5, mum_merged.shape[1]))]]

Italian Restaurant  Venue_Latitude  Venue_Longitude  \
41             0.130435       19.072488        72.826692   
41             0.130435       19.071846        72.825167   
41             0.130435       19.071756        72.825535   
41             0.130435       19.071752        72.824796   
41             0.130435       19.073264        72.826178   
41             0.130435       19.070783        72.823045   
41             0.130435       19.071727        72.824904   
41             0.130435       19.071334        72.824054   
41             0.130435       19.071989        72.825556   
41             0.130435       19.071823        72.825277   
41             0.130435       19.071206        72.823867   
41             0.130435       19.070943        72.823343   
41             0.130435       19.070973        72.823336   
41             0.130435       19.070906        72.823209   
41             0.130435       19.070962        72.823382   
41             0.130435       19.074862        72.826675   
41             0.130435       19.075005        72.827050   
41             0.130435       19.070723        72.823117   
41             0.130435       19.070853        72.823124   
41             0.130435       19.070851        72.823134   
41             0.130435       19.070919        72.823292   
41             0.130435       19.070793        72.823081   
41             0.130435       19.072196        72.828853   
113            0.116279       18.929183        72.822232   
113            0.116279       18.928426        72.822512   
113            0.116279       18.927878        72.820711   
113            0.116279       18.927878        72.820664   
113            0.116279       18.927101        72.820165   
113            0.116279       18.927910        72.820679   
113            0.116279       18.925631        72.819861   
113            0.116279       18.927144        72.820143   
113            0.116279       18.927687        72.821943   
113            0.116279       18.926465        72.822470   
113            0.116279       18.931876        72.823031   
113            0.116279       18.926525        72.820810   
113            0.116279       18.931605        72.823121   
113            0.116279       18.925063        72.819958   
113            0.116279       18.927131        72.820151   
113            0.116279       18.925257        72.819578   
113            0.116279       18.925495        72.819495   
113            0.116279       18.931964        72.824636   
113            0.116279       18.927116        72.820165   
113            0.116279       18.925134        72.819730   
113            0.116279       18.924562        72.821526   
113            0.116279       18.926086        72.820249   
113            0.116279       18.927070        72.820167   
113            0.116279       18.931465        72.822941   
113            0.116279       18.925118        72.821495   
113            0.116279       18.927874        72.820636   
113            0.116279       18.931777        72.825026   
113            0.116279       18.926468        72.822511   
113            0.116279       18.926775        72.822464   
113            0.116279       18.924512        72.822650   
113            0.116279       18.930674        72.826320   
113            0.116279       18.930320        72.826361   
113            0.116279       18.928016        72.822694   
113            0.116279       18.931567        72.822921   
113            0.116279       18.931487        72.822968   
113            0.116279       18.926448        72.822415   
113            0.116279       18.932695        72.823610   
113            0.116279       18.926274        72.822642   
113            0.116279       18.924439        72.821560   
113            0.116279       18.926731        72.820572   
113            0.116279       18.925761        72.826003   
113            0.116279       18.927245        72.820647   
113            0.116279       18.930697      

In [35]:
mum_merged.loc[mum_merged['Cluster Labels'] == 2, mum_merged.columns[[1] + list(range(5, mum_merged.shape[1]))]]

Italian Restaurant  Venue_Latitude  Venue_Longitude  \
12             0.023810       18.957445        72.813251   
12             0.023810       18.956426        72.812065   
12             0.023810       18.956605        72.813465   
12             0.023810       18.956125        72.813475   
12             0.023810       18.959689        72.811475   
12             0.023810       18.956066        72.813414   
12             0.023810       18.955931        72.812095   
12             0.023810       18.955505        72.813186   
12             0.023810       18.955405        72.814177   
12             0.023810       18.955732        72.812887   
12             0.023810       18.957452        72.809994   
12             0.023810       18.955855        72.812626   
12             0.023810       18.957481        72.813120   
12             0.023810       18.958108        72.811000   
12             0.023810       18.957492        72.808884   
12             0.023810       18.957467        72.809843   
12             0.023810       18.955360        72.813698   
12             0.023810       18.962266        72.813960   
12             0.023810       18.957074        72.810428   
12             0.023810       18.960410        72.809329   
12             0.023810       18.955519        72.814264   
12             0.023810       18.955876        72.813131   
12             0.023810       18.956000        72.814000   
12             0.023810       18.956985        72.809030   
12             0.023810       18.956796        72.816649   
12             0.023810       18.954690        72.814796   
12             0.023810       18.955298        72.813814   
12             0.023810       18.956802        72.816603   
12             0.023810       18.956510        72.815754   
12             0.023810       18.954780        72.814451   
12             0.023810       18.957283        72.810485   
12             0.023810       18.960566        72.817226   
12             0.023810       18.958839        72.810746   
12             0.023810       18.957446        72.810821   
12             0.023810       18.955020        72.816481   
12             0.023810       18.959018        72.817370   
12             0.023810       18.954042        72.814871   
12             0.023810       18.954627        72.814698   
12             0.023810       18.962246        72.813733   
12             0.023810       18.959363        72.817301   
12             0.023810       18.960256        72.816620   
12             0.023810       18.957378        72.817433   
17             0.041667       18.957445        72.813251   
17             0.041667       18.956125        72.813475   
17             0.041667       18.954113        72.815396   
17             0.041667       18.956605        72.813465   
17             0.041667       18.955405        72.814177   
17             0.041667       18.956066        72.813414   
17             0.041667       18.956426        72.812065   
17             0.041667       18.955505        72.813186   
17             0.041667       18.953616        72.815366   
17             0.041667       18.954531        72.817885   
17             0.041667       18.955732        72.812887   
17             0.041667       18.955931        72.812095   
17             0.041667       18.955360        72.813698   
17             0.041667       18.955855        72.812626   
17             0.041667       18.957481        72.813120   
17             0.041667       18.955519        72.814264   
17             0.041667       18.956796        72.816649   
17             0.041667       18.954690        72.814796   
17             0.041667       18.954825        72.817131   
17             0.041667       18.956000        72.814000   
17             0.041667       18.954235        72.818199   
17             0.041667       18.955876        72.813131   
17             0.041667       18.956802        72.816603   
17             0.041667       18.957385      

In [36]:
mum_merged.loc[mum_merged['Cluster Labels'] == 3, mum_merged.columns[[1] + list(range(5, mum_merged.shape[1]))]]

Italian Restaurant  Venue_Latitude  Venue_Longitude  \
1              0.083333       18.981231        72.817178   
1              0.083333       18.983885        72.815241   
1              0.083333       18.988617        72.814981   
1              0.083333       18.988726        72.814814   
1              0.083333       18.984465        72.815192   
1              0.083333       18.986212        72.815040   
1              0.083333       18.988536        72.815607   
1              0.083333       18.988765        72.815311   
1              0.083333       18.985247        72.815722   
1              0.083333       18.985299        72.815310   
1              0.083333       18.981116        72.816823   
1              0.083333       18.981278        72.819636   
32             0.060000       18.933478        72.824995   
32             0.060000       18.932342        72.827591   
32             0.060000       18.931964        72.824636   
32             0.060000       18.930374        72.826734   
32             0.060000       18.931966        72.828243   
32             0.060000       18.933983        72.823896   
32             0.060000       18.933500        72.826300   
32             0.060000       18.933516        72.823925   
32             0.060000       18.934892        72.824222   
32             0.060000       18.931876        72.823031   
32             0.060000       18.933629        72.823944   
32             0.060000       18.929797        72.827468   
32             0.060000       18.931605        72.823121   
32             0.060000       18.932457        72.824629   
32             0.060000       18.935049        72.824191   
32             0.060000       18.929788        72.827612   
32             0.060000       18.933526        72.825715   
32             0.060000       18.935014        72.824243   
32             0.060000       18.931777        72.825026   
32             0.060000       18.934689        72.824822   
32             0.060000       18.932948        72.826127   
32             0.060000       18.933207        72.826206   
32             0.060000       18.932605        72.827803   
32             0.060000       18.935054        72.824014   
32             0.060000       18.935090        72.824029   
32             0.060000       18.934036        72.827060   
32             0.060000       18.935131        72.826910   
32             0.060000       18.929772        72.828906   
32             0.060000       18.930674        72.826320   
32             0.060000       18.933173        72.826929   
32             0.060000       18.931465        72.822941   
32             0.060000       18.930320        72.826361   
32             0.060000       18.932817        72.827676   
32             0.060000       18.932985        72.827716   
32             0.060000       18.933294        72.826214   
32             0.060000       18.932344        72.827952   
32             0.060000       18.932040        72.828180   
32             0.060000       18.932695        72.823610   
32             0.060000       18.932549        72.827671   
32             0.060000       18.932447        72.827669   
32             0.060000       18.931567        72.822921   
32             0.060000       18.932057        72.827150   
32             0.060000       18.930697        72.826090   
32             0.060000       18.933351        72.825934   
32             0.060000       18.931487        72.822968   
32             0.060000       18.931913        72.827367   
32             0.060000       18.933566        72.824778   
32             0.060000       18.932515        72.826383   
32             0.060000       18.934706        72.827329   
32             0.060000       18.930219        72.826588   
56             0.083333       18.981231        72.817178   
56             0.083333       18.983885        72.815241   
56             0.083333       18.988617        72.814981   
56             0.083333       18.988726      

In [37]:
mum_merged.loc[mum_merged['Cluster Labels'] == 4, mum_merged.columns[[1] + list(range(5, mum_merged.shape[1]))]]

Empty DataFrame
Columns: [Italian Restaurant, Venue_Latitude, Venue_Longitude, Venue_Category]
Index: []

# As we can see above, clusters 0 and 4 are the best places to open a Italian Restaurant as they have the least amount of Italian restaurants